In [1]:
import os
from collections import defaultdict, Counter

# os.environ["CUDA_VISIBLE_DEVICES"] = "5"
# os.environ["TOKENIZERS_PARALLELISM"] = "true"
import calendar

import numpy as np
import pandas as pd
import gensim
import nltk
import spacy
import re
import torch
import torch.nn as nn
import gensim.corpora as corpora
import gensim
import string
import pyLDAvis
import pyLDAvis.gensim_models
import langid
import random

from matplotlib import pyplot as plt
from pprint import pprint
from nltk.corpus import stopwords
from nltk import tokenize
from wordcloud import WordCloud, STOPWORDS
from functools import reduce
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sentence_transformers import SentenceTransformer
from sklearn.model_selection import train_test_split, StratifiedKFold, TimeSeriesSplit
from sklearn.pipeline import Pipeline
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import roc_auc_score
from sklearn.preprocessing import StandardScaler
from sklearn.multioutput import MultiOutputClassifier
from tqdm import tqdm
from torchtext.data.utils import get_tokenizer
from torchtext.vocab import build_vocab_from_iterator
from copy import deepcopy
from transformers import (
    AutoTokenizer, AutoModelForSequenceClassification, BertTokenizer, BertModel, pipeline,
    get_linear_schedule_with_warmup
)
from datasets import Dataset
from sklearn.manifold import TSNE
from sklearn.decomposition import PCA
from umap import UMAP
from sklearn.cluster import KMeans, DBSCAN
from hdbscan import HDBSCAN
from sklearn.metrics import pairwise_distances
from bertopic import BERTopic
from IPython.display import Image

torch.manual_seed(42)
torch.backends.cuda.deterministic = True

%matplotlib inline

In [2]:
from tqdm import tqdm

tqdm.pandas()

# Topic modeling

Loading data and tokenizers.

In [3]:
df = pd.read_csv('./data/processed_dataset.csv', usecols=['channelname', 'token_text'])
df

channelname                                         token_text
0      kyivpolitics                               отбой угрозы столицы
1      kyivpolitics  8 перекрестках пилотном режиме внедрят смежную...
2      kyivpolitics  нбу отозвал банковскую лицензию конкорд банка ...
3      kyivpolitics  завтра синоптики прогнозируют небольшой дождь ...
4      kyivpolitics                              снятый советский герб
...             ...                                                ...
28914     hmarochos  художницю зобовʼязали замалювати мурал січових...
28915     hmarochos  львів хоче отримати 50 євро реконструкцію вули...
28916     hmarochos  набережно хрещатицькій самовільно влаштували п...
28917   semenovatut             залишити пушкіна об єктом перформансів
28918   darnicalive                              москва сіті бавовняно

[28919 rows x 2 columns]

In [4]:
indices = df['channelname'] == 'obolonlife'

In [5]:
tokenizers = {
    'uk': spacy.load("uk_core_news_sm"),
    'ru': spacy.load("ru_core_news_sm")
}

In [6]:
all_stopwords_puncts = (tokenizers['ru'].Defaults.stop_words |
                        set(string.punctuation) |
                        tokenizers['uk'].Defaults.stop_words)

## LDA

Text preprocessing

In [7]:
docs = []
for d in tqdm(df[indices]['token_text'].to_list()):
    docs.append(
        [el.lower() for el in tokenize.word_tokenize(d) if el.lower() not in all_stopwords_puncts]
    )

100%|██████████| 1036/1036 [00:00<00:00, 10839.59it/s]


Building dictionary and applying Bag-of-words transformation

In [8]:
# Create Dictionary
vocab = corpora.Dictionary(docs)
# doc2bow means Doc transformed to Bag of Words
corpus = [vocab.doc2bow(text) for text in docs]
# View
print(
    f"Text:\n{' '.join(docs[0])}\n\n"
    f"Text BOW:\n{corpus[0]}"
)

Text:
набу проводить обшуки приміщеннях департаменту земельних ресурсів кмда яке очолює валентина пелих профільного заступника кмда земельних питань петра оленича

Text BOW:
[(0, 1), (1, 1), (2, 1), (3, 2), (4, 2), (5, 1), (6, 1), (7, 1), (8, 1), (9, 1), (10, 1), (11, 1), (12, 1), (13, 1), (14, 1), (15, 1), (16, 1)]


In [9]:
# number of topics
num_topics = 20
# Build LDA model
lda_model = gensim.models.LdaModel(
    corpus=corpus,
    id2word=vocab,
    num_topics=num_topics,
    alpha='auto',
    eta='auto',
)
# Print the Keyword in the 40 topics
pprint(lda_model.print_topics())
doc_lda = lda_model[corpus]

[(0,
  '0.006*"івасюка" + 0.005*"героїв" + 0.004*"дніпра" + 0.004*"оболонського" + '
  '0.003*"володимира" + 0.003*"проспекту" + 0.003*"просп" + 0.003*"тож" + '
  '0.003*"вечір" + 0.003*"оболонь"'),
 (1,
  '0.006*"івасюка" + 0.005*"пишуть" + 0.004*"просп" + 0.003*"поліції" + '
  '0.002*"кмда" + 0.002*"оболоні" + 0.002*"сільпо" + 0.002*"20" + '
  '0.002*"героїв" + 0.002*"метро"'),
 (2,
  '0.008*"оболоні" + 0.006*"оболонь" + 0.005*"героїв" + 0.005*"дніпра" + '
  '0.003*"вулиці" + 0.003*"доброго" + 0.003*"пишуть" + 0.003*"оболонському" + '
  '0.002*"ранок" + 0.002*"ранку"'),
 (3,
  '0.010*"івасюка" + 0.007*"просп" + 0.005*"володимира" + 0.004*"героїв" + '
  '0.004*"дніпра" + 0.003*"бюджету" + 0.003*"проспекту" + 0.003*"руху" + '
  '0.003*"степана" + 0.003*"бандери"'),
 (4,
  '0.005*"героїв" + 0.004*"дніпра" + 0.004*"оболонь" + 0.003*"вулиці" + '
  '0.003*"місці" + 0.003*"оболонському" + 0.003*"слава" + 0.002*"будинку" + '
  '0.002*"міста" + 0.002*"пишуть"'),
 (5,
  '0.008*"оболонь" + 0.00

In [10]:
# Visualize the topics
pyLDAvis.enable_notebook()

LDAvis_prepared = pyLDAvis.gensim_models.prepare(lda_model, corpus, vocab)
LDAvis_prepared

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
3     -0.146889 -0.084330       1        1  9.331687
11     0.007176 -0.031498       2        1  7.676740
18     0.000959 -0.044950       3        1  6.439873
16     0.038758  0.010740       4        1  6.288819
10     0.015616 -0.057235       5        1  6.131287
7      0.033462 -0.014896       6        1  5.460348
8     -0.039556  0.022013       7        1  5.420757
19    -0.036580  0.045321       8        1  5.158058
13     0.011810 -0.019358       9        1  4.875280
5      0.031755 -0.010211      10        1  4.761135
9      0.054288 -0.071192      11        1  4.736592
2      0.034317 -0.006431      12        1  4.382042
17     0.051935  0.026605      13        1  4.365672
0     -0.005751 -0.011155      14        1  4.341653
1     -0.017706 -0.028211      15        1  4.233210
4      0.007706  0.053726      16        1  4.098161
15    -0.005215  0.045883      17        1  3.832825
6     -0.084069  0.095881      18        1  3.684777
14     0.025914  0.056043      19        1  2.663244
12     0.022070  0.023254      20        1  2.117840, topic_info=              Term       Freq      Total Category  logprob  loglift
103        оболоні  85.000000  85.000000  Default  30.0000  30.0000
68         івасюка  88.000000  88.000000  Default  29.0000  29.0000
234        оболонь  80.000000  80.000000  Default  28.0000  28.0000
23           вечір  26.000000  26.000000  Default  27.0000  27.0000
889         героїв  77.000000  77.000000  Default  26.0000  26.0000
...            ...        ...        ...      ...      ...      ...
2500       просимо   0.972346  20.787865  Topic20  -6.3544   0.7924
234        оболонь   1.133940  80.129745  Topic20  -6.2006  -0.4032
2510        вечора   0.909962  18.748600  Topic20  -6.4207   0.8293
2110        сміття   0.866066  15.575648  Topic20  -6.4701   0.9653
668   оболонського   0.882186  39.646547  Topic20  -6.4517   0.0494

[1537 rows x 6 columns], token_table=      Topic      Freq          Term
term                               
1564      5  0.092445            09
1564      6  0.092445            09
1564      7  0.092445            09
1564      9  0.092445            09
1564     11  0.092445            09
...     ...       ...           ...
1861     13  0.098414    інформація
1861     15  0.098414    інформація
1861     16  0.196828    інформація
9623     15  0.807850  ініційованої
69       15  0.534540        їздили

[3525 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[4, 12, 19, 17, 11, 8, 9, 20, 14, 6, 10, 3, 18, 1, 2, 5, 16, 7, 15, 13])

## BERDTopic
### Llama 2

As last step in BERTopic pipeline was decided to use Llama 2 model. We use the smallest model with 7B parameters, finetuned for chat conversation.

In [11]:
model_id = 'meta-llama/Llama-2-7b-chat-hf'

The prompt for llm consists of three parts: system prompt, example prompt, main prompt.
In system prompt we described what llm should do and in what style it should answer:

In [12]:
system_prompt_en = """
[INST] <<SYS>>
You are a helpful, respectful and honest guide to finding the general topic of given documents and keywords. You return only the topic stamp and nothing else.
<</SYS>>
"""

In example prompt we show the example of conversation and the desired answer:

In [13]:
example_prompt_en = """
I have a topic that contains the following documents:
- Traditional diets in most cultures consisted mostly of plant foods with a small amount of meat, but with the development of industrialized meat production and factory farming, meat became a staple food.
- Meat, but especially beef, is the best food in terms of emissions.
- Eating meat does not make you a bad person, not having meat does not make you a good person.

The topic is described by the following keywords: 'meat, beef, eat, eat, emissions, steak, food, health, processed, chicken'.

Based on the topic information above, create a short tag for that topic. Make sure you only return the label and nothing else.

[/INST] The impact of eating meat on the environment
"""

In main prompt we set the template in which BERTopic will pass representing documents (`[DOCUMENTS]`) and keywords (`[KEYWORDS]`)

In [14]:
main_prompt_en = """
[INST]
I have a topic that contains the following documents:
[DOCUMENTS]

The topic is described by the following keywords: '[KEYWORDS]'.

Based on the topic information above, create a short tag for that topic. Make sure you only return the label and nothing else.
[/INST]
"""

In [15]:
prompt_en = system_prompt_en + example_prompt_en + main_prompt_en

Loading Llama 2

In [16]:
from torch import bfloat16
import transformers

# set quantization configuration to load large model with less GPU memory
# this requires the `bitsandbytes` library

bnb_config = transformers.BitsAndBytesConfig(
    load_in_4bit=True,  # 4-bit quantization
    bnb_4bit_quant_type='nf4',  # Normalized float 4
    bnb_4bit_use_double_quant=True,  # Second quantization after the first
    bnb_4bit_compute_dtype=bfloat16  # Computation type
)

In [17]:
# Llama 2 Tokenizer
tokenizer = transformers.AutoTokenizer.from_pretrained(model_id)

# Llama 2 Model
model = transformers.AutoModelForCausalLM.from_pretrained(
    model_id,
    trust_remote_code=True,
    quantization_config=bnb_config,
)
model.eval()

bin C:\Users\Andrii\anaconda3\envs\IASA_NLP\Lib\site-packages\bitsandbytes\libbitsandbytes_cuda121.dll


Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

LlamaForCausalLM(
  (model): LlamaModel(
    (embed_tokens): Embedding(32000, 4096)
    (layers): ModuleList(
      (0-31): 32 x LlamaDecoderLayer(
        (self_attn): LlamaAttention(
          (q_proj): Linear4bit(in_features=4096, out_features=4096, bias=False)
          (k_proj): Linear4bit(in_features=4096, out_features=4096, bias=False)
          (v_proj): Linear4bit(in_features=4096, out_features=4096, bias=False)
          (o_proj): Linear4bit(in_features=4096, out_features=4096, bias=False)
          (rotary_emb): LlamaRotaryEmbedding()
        )
        (mlp): LlamaMLP(
          (gate_proj): Linear4bit(in_features=4096, out_features=11008, bias=False)
          (up_proj): Linear4bit(in_features=4096, out_features=11008, bias=False)
          (down_proj): Linear4bit(in_features=11008, out_features=4096, bias=False)
          (act_fn): SiLUActivation()
        )
        (input_layernorm): LlamaRMSNorm()
        (post_attention_layernorm): LlamaRMSNorm()
      )
    )
    (norm

Forming generation pipeline

In [18]:
generator = transformers.pipeline(
    model=model, tokenizer=tokenizer,
    task='text-generation',
    temperature=0.75,
    max_new_tokens=15,
    repetition_penalty=1.1,
    top_p=0.9
)

### Text preprocessing

In order to increase model performance, was decided to delete some percent of most common words for current cluster:

In [19]:
def get_most_common_words(series, num_common_words=None):
    combined_text = series.str.cat(sep=' ')

    words = combined_text.split()
    word_counts = Counter(words)
    vocab = list(word_counts.keys())
    if num_common_words is None:
        num_common_words = int(len(word_counts) * 0.001)
    print(len(word_counts))

    # Get the most common words
    most_common_words = word_counts.most_common(num_common_words)

    return [word[0] for word in most_common_words]

In [20]:
indices = df['channelname'] == 'novynylive'

In [21]:
texts = df[indices]['token_text']

In [22]:
new_stop_words = set(get_most_common_words(texts))
new_stop_words

26643


{'атаки',
 'відео',
 'війни',
 'заявив',
 'змі',
 'зсу',
 'людей',
 'наразі',
 'об',
 'області',
 'оборони',
 'ова',
 'окупанти',
 'повідомив',
 'понад',
 'росіяни',
 'росії',
 'рф',
 'сили',
 'сша',
 'україна',
 'хамас',
 'чоловік',
 'єс',
 'ізраїль',
 'ізраїлю'}

In [23]:
texts = texts.progress_apply(
    lambda x: ' '.join([token.text for token in tokenizers['uk'](x) if token.text not in new_stop_words])
    )
get_most_common_words(texts, 10)

100%|██████████| 3548/3548 [00:29<00:00, 118.74it/s]

26617


['внаслідок',
 'напрямку',
 'окупантів',
 'куп',
 'вибухи',
 'словами',
 'даними',
 'зокрема',
 'новини',
 'удару']

### Topic modeling

In [30]:
from bertopic import BERTopic
from bertopic.representation import TextGeneration, KeyBERTInspired, MaximalMarginalRelevance
from bertopic.vectorizers import ClassTfidfTransformer

embedding_model = SentenceTransformer("sentence-transformers/distiluse-base-multilingual-cased-v2") # loading sentence-transformers model
embeddings = embedding_model.encode(texts.to_list()) # precompute sentence embeddings
reduced_embeddings = UMAP(n_neighbors=int(0.02 * len(texts)), n_components=2, min_dist=0.0, metric='cosine', random_state=42).fit_transform(
    embeddings
    ) # build reduced embeddings for future visualisation

umap_model = UMAP(n_neighbors=int(0.02 * len(texts)), n_components=8, min_dist=0.0, metric='cosine', random_state=42)  # set parameters for UMAP algorithm
hdbscan_model = HDBSCAN(min_cluster_size=int(0.01 * len(texts)), metric='euclidean', cluster_selection_method='eom', prediction_data=True)  # set parameters for HDBSCAN algorithm

ctfidf_model = ClassTfidfTransformer(
    bm25_weighting=True
    # reduce_frequent_words=True
)

# Initialize 3 different representation models
keybert = KeyBERTInspired()
mmr = MaximalMarginalRelevance(diversity=0.3)
llama2 = TextGeneration(generator, prompt=prompt_en)

representation_model = {
    "KeyBERT": keybert,
    "Llama2": llama2,
    "MMR": mmr,
}

topic_model = BERTopic(
    embedding_model=embedding_model,
    umap_model=umap_model,
    hdbscan_model=hdbscan_model,
    ctfidf_model=ctfidf_model,
    representation_model=representation_model,

    verbose=True,
)

In [31]:
topics, probs = topic_model.fit_transform(texts.to_list(), embeddings=embeddings)

2023-11-12 22:53:37,258 - BERTopic - Reduced dimensionality
C:\Users\Andrii\anaconda3\envs\IASA_NLP\Lib\site-packages\hdbscan\hdbscan_.py:1170: DeprecationWarning:

`alltrue` is deprecated as of NumPy 1.25.0, and will be removed in NumPy 2.0. Please use `all` instead.

2023-11-12 22:53:37,359 - BERTopic - Clustered reduced embeddings
100%|██████████| 16/16 [00:14<00:00,  1.09it/s]


In [32]:
topic_model.get_topic_info()

Topic  Count                                            Name  \
0      -1   1754            -1_окупантів_росія_жовтня_російських   
1       0    353          0_внаслідок_річний_обстрілу_пошкоджено   
2       1    224                1_вибухи_місцеві_пабліки_лунають   
3       2    221                        2_гази_газі_ізраїлі_газа   
4       3    216                  3_затримали_підозру_000_кордон   
5       4    153          4_повітряні_застосування_бпла_напрямку   
6       5    121        5_українських_українців_україну_біженців   
7       6     97  6_українців_українські_українських_український   
8       7     84          7_російських_росзмі_російського_росіян   
9       8     81                    8_львові_львова_львів_центрі   
10      9     53                    9_партії_виборах_прем_вибори   
11     10     41            10_моніторингові_канали_вибухи_групи   
12     11     39              11_ремонт_тендер_планують_prozorro   
13     12     37                     12_європи_світу_уєфа_медалі   
14     13     37                 13_омбр_бійці_окупантів_бригади   
15     14     37                   14_прямий_ефір_міністр_штатів   

                                       Representation  \
0   [окупантів, росія, жовтня, російських, млрд, к...   
1   [внаслідок, річний, обстрілу, пошкоджено, райо...   
2   [вибухи, місцеві, пабліки, лунають, вибух, хер...   
3   [гази, газі, ізраїлі, газа, цахал, хамасу, сек...   
4   [затримали, підозру, 000, кордон, тцк, тис, ви...   
5   [повітряні, застосування, бпла, напрямку, загр...   
6   [українських, українців, україну, біженців, ук...   
7   [українців, українські, українських, українськ...   
8   [російських, росзмі, російського, росіян, удар...   
9   [львові, львова, львів, центрі, live, новини, ...   
10  [партії, виборах, прем, вибори, палати, єр, ви...   
11  [моніторингові, канали, вибухи, групи, повідом...   
12  [ремонт, тендер, планують, prozorro, дороги, к...   
13  [європи, світу, уєфа, медалі, футболу, чемпіон...   
14  [омбр, бійці, окупантів, бригади, дук, ої, 67,...   
15  [прямий, ефір, міністр, штатів, зеленський, мі...   

                                              KeyBERT  \
0   [російські, росія, російських, росіян, військо...   
1   [поранених, постраждалі, постраждали, пораненн...   
2   [вибухів, вибухи, дніпропетровщині, місцеві, о...   
3   [газі, хамасу, газа, палестинців, палестинці, ...   
4   [000, правоохоронці, військовозобов, незаконно...   
5   [загроза, загрозу, небезпека, бомбардувальникі...   
6   [українці, українськими, українським, українця...   
7   [українцями, українці, українськими, українськ...   
8   [росія, росзмі, російські, російська, росіян, ...   
9   [львові, львова, львів, львівському, львівсько...   
10  [парламентських, парламенті, парламенту, вибор...   
11  [моніторингові, канали, вибухи, tv, telegraph,...   
12  [ремонту, ремонт, відремонтувати, реконструкці...   
13  [медаль, медалей, медаллю, чемпіонат, турнірів...   
14  [артилерійських, артилерійська, артилерія, 92,...   
15  [вибори, демократію, сенаті, прямий, мобілізац...   

                                               Llama2  \
0                [Russian Invasion, , , , , , , , , ]   
1                  [War in Ukraine, , , , , , , , , ]   
2    [Explosions in various cities, , , , , , , , , ]   
3            [Israel-Gaza conflict, , , , , , , , , ]   
4   ["Coordination of illegal border crossing", , ...   
5                [Airborne Threats, , , , , , , , , ]   
6              [Ukrainian Refugees, , , , , , , , , ]   
7   [Ukrainian casualties in Israel, , , , , , , ,...   
8       [Russian Attack on Kharkiv, , , , , , , , , ]   
9                          [Levova, , , , , , , , , ]   
10                [Polish politics, , , , , , , , , ]   
11  [Explosions monitored in Ukraine, , , , , , , ...   
12  [Reconstruction and repair of roads, , , , , ,...   
13  [Championships and Medals in Europe, , , , , ,...   
14      [Ukrainian Military Forces, , , , , , , , , 

In [33]:
llama2_labels = [label[0][0].split("\n")[0] for label in topic_model.get_topics(full=True)["Llama2"].values()]
topic_model.set_topic_labels(llama2_labels)

In [34]:
topic_model.visualize_documents(texts.tolist(), reduced_embeddings=reduced_embeddings, hide_annotations=True, hide_document_hover=False, custom_labels=True)

In [35]:
topic_model.visualize_topics()

Interim conclusion:

On the 'Documents and Topics' plot, the BERTopic model performed well, producing several high-quality clusters with similar texts. Additionally, it is evident that Llama 2 7B can be used to form topic names. 
However, upon examining the 'Intertopic Distance Map,' it may be beneficial to reduce the number of topics to 3-4.

### Postprocessing

As a post-processing attempt, I tried using Llama 2 to match the predicted topics to one of the "big ones" given in the homework assignment.

In [36]:
from transformers import TextGenerationPipeline


def get_topic(gen: TextGenerationPipeline, keywords:list[str]):
    topic_prompt = f'''
[INST] <<SYS>>
You are a helpful, respectful and honest helper for marking topics. You map given keywords to one of next categories: [(Adult), (Art), (Blogs), (Bookmaking), (Books), (Business and startups), (Career), (Courses and guides), (Cryptocurrencies), (Darknet), (Design), (Economics), (Education), (Edutainment), (Erotic), (Esoterics), (Family & Children), (Fashion and beauty), (Food and cooking), (Games), (Handiwork), (Health and Fitness), (Humor and entertainment), (Instagram), (Interior and construction), (Law), (Linguistics), (Marketing, PR, advertising), (Medicine), (Music), (Nature), (News and media), (Other), (Pictures and photos), (Politics), (Psychology), (Quotes), (Religion), (Sales), (Shock content), (Software & Applications), (Sport), (Technologies), (Telegram), (Transport), (Travel), (Video and films)].
You answer only exact category name (from list above) and nothing else.
<</SYS>>
Keywords: [війна, осбстріли, шахеди, окупанти, зіткнення, танки, бмп]
Category: 
[/INST]War
[INST]
Keywords: [{', '.join(keywords)}]
Category: 
[/INST]
'''
    gen_text = gen(topic_prompt)[0]['generated_text']
    topic = gen_text.replace(topic_prompt, '') + '\n\n'
    topic = topic.partition('\n\n')[0]
    topic = topic.strip()
    return topic

In [40]:
def get_topics_and_subtopics(gen, topic_df, representation_column='Representation', llm_column='Llama2'):
    result_topics = defaultdict(list)
    
    for index, row in topic_df.iterrows():
        big_topic = get_topic(gen, row[representation_column])
        sub_topic = row[llm_column][0]
        sub_topic = sub_topic.replace('#', '')
        sub_topic = sub_topic.removeprefix('"').removeprefix("'")
        sub_topic = sub_topic.removesuffix('"').removesuffix("'")
        
        result_topics[big_topic].append(sub_topic)
    return result_topics

In [41]:
topics_df = topic_model.get_topic_info()

In [42]:
get_topics_and_subtopics(generator, topics_df, representation_column='MMR')

defaultdict(list,
            {'Russia': ['Russian Invasion', 'Russian Attack on Kharkiv'],
             'Violence': ['War in Ukraine'],
             'Local News': ['Explosions in various cities'],
             'I apologize, but I cannot provide information or answers that promote hate speech': ['Israel-Gaza conflict'],
             'Court': ['Coordination of illegal border crossing'],
             'Air Strikes': ['Airborne Threats'],
             'Politics': ['Ukrainian Refugees',
              'Ukrainian casualties in Israel',
              'Polish politics',
              'Political Elections and Direct Broadcasting'],
             'Lions': ['Levova'],
             'Renewable Energy': ['Explosions monitored in Ukraine'],
             'Construction': ['Reconstruction and repair of roads'],
             'Sports': ['Championships and Medals in Europe'],
             'War': ['Ukrainian Military Forces']})

As we can see above, Llama 2 7B is not enough to solve such a task. Although, it can understand global topic meaning, Llama 2 7B can't assign the label correctly. May be it can be improved by using llama 2 13B or other bigger LLM.